# Set up imports

In [3]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [4]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [5]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [6]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [20]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [21]:
data = df.abstract.values.tolist()

In [22]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [23]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [24]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [25]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [26]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [27]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [28]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=5, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [29]:
#ldaseq.print_topics(time=0) # at timeslice 1, those are the topics, word probability to the right 

[[('model', 0.033578317379155405),
  ('data', 0.01644256549749222),
  ('method', 0.01241790945768683),
  ('inference', 0.011170967773255344),
  ('distribution', 0.009821696357877361),
  ('structure', 0.007593979768173603),
  ('approach', 0.007426731873022371),
  ('process', 0.007393721090963855),
  ('variable', 0.0071264047491648086),
  ('bayesian', 0.006954092319707852),
  ('algorithm', 0.006877250876636638),
  ('latent', 0.006150550177586438),
  ('graph', 0.005637512798633828),
  ('show', 0.005584177789209771),
  ('using', 0.0053645180220157525),
  ('probabilistic', 0.005305460376111756),
  ('learning', 0.00494322219138251),
  ('based', 0.004774639272230274),
  ('prior', 0.004754277721274941),
  ('problem', 0.004678325991937516)],
 [('image', 0.021761350016033573),
  ('model', 0.020185866085484103),
  ('feature', 0.013704186017350703),
  ('object', 0.011878891407934213),
  ('task', 0.009928259343266984),
  ('learning', 0.009427739934282814),
  ('method', 0.008175574283143413),
  ('da

In [30]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('model', 0.033578317379155405),
  ('data', 0.01644256549749222),
  ('method', 0.01241790945768683),
  ('inference', 0.011170967773255344),
  ('distribution', 0.009821696357877361),
  ('structure', 0.007593979768173603),
  ('approach', 0.007426731873022371),
  ('process', 0.007393721090963855),
  ('variable', 0.0071264047491648086),
  ('bayesian', 0.006954092319707852),
  ('algorithm', 0.006877250876636638),
  ('latent', 0.006150550177586438),
  ('graph', 0.005637512798633828),
  ('show', 0.005584177789209771),
  ('using', 0.0053645180220157525),
  ('probabilistic', 0.005305460376111756),
  ('learning', 0.00494322219138251),
  ('based', 0.004774639272230274),
  ('prior', 0.004754277721274941),
  ('problem', 0.004678325991937516)],
 [('model', 0.03370945790262112),
  ('data', 0.01648666884076272),
  ('method', 0.012451940997219893),
  ('inference', 0.011199672045613809),
  ('distribution', 0.00984569960410411),
  ('structure', 0.007609896876629546),
  ('approach', 0.007442541538299481

In [40]:
ldaseq.print_topic_times(topic=1) 

[[('image', 0.021761350016033573),
  ('model', 0.020185866085484103),
  ('feature', 0.013704186017350703),
  ('object', 0.011878891407934213),
  ('task', 0.009928259343266984),
  ('learning', 0.009427739934282814),
  ('method', 0.008175574283143413),
  ('data', 0.007908353683383563),
  ('approach', 0.007764763632704053),
  ('training', 0.007645348356510925),
  ('visual', 0.0063551572774394145),
  ('representation', 0.005873089572661453),
  ('using', 0.005678805033738668),
  ('show', 0.005230152533832777),
  ('human', 0.005222075605323756),
  ('recognition', 0.005148575576857263),
  ('result', 0.0050613993746785714),
  ('two', 0.00470879161022025),
  ('performance', 0.00469612006385825),
  ('classification', 0.004563394145845678)],
 [('image', 0.021670419411662933),
  ('model', 0.02017231486901091),
  ('feature', 0.013807538485457207),
  ('object', 0.011900356146943288),
  ('task', 0.009986075781010503),
  ('learning', 0.009451622339774033),
  ('method', 0.008217309729525406),
  ('data'

In [41]:
ldaseq.print_topic_times(topic=2) 

[[('algorithm', 0.022682457728853182),
  ('bound', 0.014786722208142516),
  ('problem', 0.011788816744619688),
  ('function', 0.009855857823804432),
  ('matrix', 0.008485562213592927),
  ('method', 0.008324072490949236),
  ('show', 0.008172909019123811),
  ('result', 0.007203828266337323),
  ('rate', 0.007140673425824774),
  ('gradient', 0.006728315557968153),
  ('convergence', 0.006207032719676197),
  ('sample', 0.005767357309319276),
  ('distribution', 0.005646842104148403),
  ('analysis', 0.00561236392857912),
  ('complexity', 0.005426268484852258),
  ('regret', 0.005251611879022856),
  ('estimation', 0.005044106612528294),
  ('stochastic', 0.004898613232744547),
  ('also', 0.004777456635705999),
  ('error', 0.004746436747116545)],
 [('algorithm', 0.022637190449588868),
  ('bound', 0.014836854995486674),
  ('problem', 0.011824268702248541),
  ('function', 0.009884294619594638),
  ('matrix', 0.008507937347642184),
  ('method', 0.008345568697637104),
  ('show', 0.008193855630412934),


In [42]:
ldaseq.print_topic_times(topic=3) 

[[('algorithm', 0.025488061157108565),
  ('learning', 0.02050906342918482),
  ('problem', 0.017592606728893484),
  ('method', 0.013511396962218945),
  ('data', 0.012936054580507332),
  ('function', 0.009394232674167544),
  ('kernel', 0.008700042875936504),
  ('show', 0.007821057390405086),
  ('approach', 0.007128281227354098),
  ('paper', 0.006076843458143813),
  ('result', 0.005876250072209107),
  ('set', 0.00523118928815245),
  ('based', 0.004840308924200506),
  ('clustering', 0.004806026776216593),
  ('performance', 0.004609363394815711),
  ('proposed', 0.004582522574639038),
  ('optimization', 0.004534614356834136),
  ('new', 0.004396210168463084),
  ('propose', 0.004253001941913759),
  ('classification', 0.004176919591548125)],
 [('algorithm', 0.025582044847988754),
  ('learning', 0.020572014635808007),
  ('problem', 0.017643846375449364),
  ('method', 0.013547432784917175),
  ('data', 0.012974125972582514),
  ('function', 0.009414846615941568),
  ('kernel', 0.008720076464788609),

In [43]:
ldaseq.print_topic_times(topic=4) 

[[('model', 0.0132305859797695),
  ('neural', 0.01000066449819994),
  ('network', 0.009010624086894166),
  ('learning', 0.008617574970433525),
  ('neuron', 0.007711910613555682),
  ('policy', 0.007574577891203729),
  ('state', 0.007225366207639733),
  ('system', 0.006399734251051841),
  ('show', 0.006377068722082882),
  ('stimulus', 0.006038133289017908),
  ('time', 0.005841102360972893),
  ('dynamic', 0.0056419967463967645),
  ('information', 0.00515424920696679),
  ('control', 0.004805208485664637),
  ('using', 0.00478130131674619),
  ('spike', 0.004640412849215529),
  ('activity', 0.004614331135297404),
  ('action', 0.004490663524358231),
  ('response', 0.004475238016268169),
  ('decision', 0.004382217312450107)],
 [('model', 0.013260563274774316),
  ('neural', 0.009904875974018115),
  ('network', 0.008940751408534267),
  ('learning', 0.008644830478063692),
  ('neuron', 0.007746331368637359),
  ('policy', 0.007607977442455951),
  ('state', 0.007256073414665705),
  ('show', 0.0064021

In [31]:
# to check Document - Topic proportions, use `doc-topics`
#doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
#print (doc)
# this document is made up of different topics like this

[8.59018397e-01 1.40426561e-01 1.85013876e-04 1.85013876e-04
 1.85013876e-04]


In [32]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [39]:
ldaseq.print_topic_times(1) # evolution of 2nd topic through all timeslices


[[('image', 0.021761350016033573),
  ('model', 0.020185866085484103),
  ('feature', 0.013704186017350703),
  ('object', 0.011878891407934213),
  ('task', 0.009928259343266984),
  ('learning', 0.009427739934282814),
  ('method', 0.008175574283143413),
  ('data', 0.007908353683383563),
  ('approach', 0.007764763632704053),
  ('training', 0.007645348356510925),
  ('visual', 0.0063551572774394145),
  ('representation', 0.005873089572661453),
  ('using', 0.005678805033738668),
  ('show', 0.005230152533832777),
  ('human', 0.005222075605323756),
  ('recognition', 0.005148575576857263),
  ('result', 0.0050613993746785714),
  ('two', 0.00470879161022025),
  ('performance', 0.00469612006385825),
  ('classification', 0.004563394145845678)],
 [('image', 0.021670419411662933),
  ('model', 0.02017231486901091),
  ('feature', 0.013807538485457207),
  ('object', 0.011900356146943288),
  ('task', 0.009986075781010503),
  ('learning', 0.009451622339774033),
  ('method', 0.008217309729525406),
  ('data'

In [37]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.730720034269055
CV1 0.3869805705734364
U_Mass2 -1.7325287477271316
CV2 0.3869805705734364
U_Mass3 -1.730877728104457
CV3 0.3868185587358319
U_Mass4 -1.765352911448926
CV4 0.38675151884755515
U_Mass5 -1.7067940503565502
CV5 0.3885161441223818
U_Mass6 -1.669466749011813
CV6 0.3805115923418092
U_Mass7 -1.7453628586575913
CV7 0.39361335774789497
U_Mass8 -1.7575004996302972
CV8 0.39050757412187964
U_Mass9 -1.7632505886988181
CV9 0.3904570214143594
U_Mass10 -1.69870415250508
CV10 0.39807873753139056
U_Mass11 -1.738118716145556
CV11 0.3941512405152916
U_Mass12 -1.7405647163187463
CV12 0.3939229236454894


In [ ]:
#graph coherence and topic distribution per time slice

In [ ]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/